In [1]:
import plotly.io as pio

import Config.constants as cnst
import Analysis.Detector_Comparisons.helpers as hlp
import Analysis.figures as figs

pio.renderers.default = "notebook"

In [ ]:
DATASET = "Lund2013"
COL_MAPPER = lambda col: col[:col.index("ector")] if "ector" in col else col
VERBOSE = True
SHOW_DISTRIBUTIONS = True

In [2]:
%%capture --no-stdout

_, events, _, event_matches, comparison_columns = hlp.preprocess_dataset(DATASET,
                                                                         column_mapper=COL_MAPPER,
                                                                         verbose=VERBOSE)

events = events.map(lambda cell: [e for e in cell if e.event_label == cnst.EVENT_LABELS.SACCADE])
event_matches = event_matches.map(
    lambda cell: {k: v for k, v in cell.items() if k.event_label == cnst.EVENT_LABELS.SACCADE}
    if cell is not None else None)

comparison_columns

Preprocessing dataset `Lund2013`...
	Preprocessing:	53.63s


In [3]:
event_features = hlp.extract_features(events, verbose=VERBOSE)
event_matching_ratios = hlp.calc_event_matching_ratios(events, event_matches, verbose=VERBOSE)
event_matching_feature_diffs = hlp.calc_matched_events_feature(event_matches, verbose=VERBOSE)

	Extracting Countss:	0.20s
	Extracting Peak Velocitys:	0.14s
	Extracting Amplitudes:	0.26s
	Extracting Azimuths:	0.14s
	Extracting Durations:	0.03s
Total time:	0.78s
Total time:	0.07s

	Calculating Matched Peak Velocity:	0.18s
	Calculating Matched Overlap Time:	0.06s
	Calculating Matched Amplitude:	0.35s
	Calculating Matched Onset Jitter:	0.03s
	Calculating Matched IoU:	0.05s
	Calculating Matched L2 Timing Jitter:	0.06s
	Calculating Matched Offset Jitter:	0.03s
	Calculating Matched Azimuth:	0.17s
	Calculating Matched Duration:	0.03s
Total time:	0.96s


# Saccades' Feature Distributions

In [4]:
print(f"Available saccade features: {list(event_features.keys())}")

Available saccade features: ['Counts', 'Peak Velocity', 'Amplitude', 'Azimuth', 'Duration']


In [5]:
if SHOW_DISTRIBUTIONS:
    for feature in event_features.keys():
        if feature=="Counts":
            continue
        title = f"{DATASET.upper()}:\t\tSaccades' {feature.title()} Distribution"
        figs.distributions_grid(
            data=event_features[feature],
            title=title,
            show_counts=feature == "Counts",
        ).show()

# Matched-Saccades' Feature Differences

In [6]:
print(f"Available matched-saccade feature differences: {list(event_matching_feature_diffs.keys())}")

Available matched-saccade feature differences: ['Peak Velocity', 'Overlap Time', 'Amplitude', 'Onset Jitter', 'IoU', 'L2 Timing Jitter', 'Offset Jitter', 'Azimuth', 'Duration']


In [7]:
if SHOW_DISTRIBUTIONS:
    figs.distributions_grid(
        data=event_matching_ratios["Match Ratio"][comparison_columns],
        title=f"{DATASET.upper()}:\t\tSaccade-Matching Ratios",
        pdf_min_val=0,
        pdf_max_val=100,
        column_title_mapper=lambda col: f"{col[0]}→{col[1]}"
    ).show()

In [8]:
if SHOW_DISTRIBUTIONS:
    for feature in event_matching_feature_diffs.keys():
        figs.distributions_grid(
            data=event_matching_feature_diffs[feature][comparison_columns],
            title=f"{DATASET.upper()}:\t\tMatched-Saccades' {feature.title()} Distribution",
            column_title_mapper=lambda col: f"{col[0]}→{col[1]}",
            pdf_min_val=0 if feature == "IoU" else None,
            pdf_max_val=1 if feature == "IoU" else None,
        ).show()